# *Components* dans LlamaIndex

Ce notebook fait parti du cours <a href="https://huggingface.co/learn/agents-course/fr">sur les agents d'Hugging Face</a>, un cours gratuit qui vous guidera, du **niveau débutant à expert**, pour comprendre, utiliser et construire des agents.

![Agents course share](https://huggingface.co/datasets/agents-course/course-images/resolve/main/en/communication/share.png)

Alfred organise une fête et doit pouvoir trouver des informations pertinentes sur les personnes qui y assisteront. Nous allons donc utiliser un `QueryEngine` pour indexer et rechercher dans une base de données de personnes.

## Installons les dépendances

Nous allons installer les dépendances pour cette unité.

In [ ]:
!pip install llama-index datasets llama-index-callbacks-arize-phoenix arize-phoenix llama-index-vector-stores-chroma llama-index-llms-huggingface-api llama-index-embeddings-huggingface -U -q

Nous allons également nous connecter au Hugging Face Hub pour avoir accès à l'API d'inférence.

In [ ]:
from huggingface_hub import login

login()

## Créer un `QueryEngine` pour la RAG

### Mise en place de la base de données de personas

Nous utiliserons les personas de [dvilasuero/finepersonas-v0.1-tiny dataset](https://huggingface.co/datasets/dvilasuero/finepersonas-v0.1-tiny). Ce jeu de données contient 5K personas qui participeront à la fête !

Chargeons le jeu de données et stockons-le sous forme de fichiers dans le répertoire `data`.

In [6]:
from datasets import load_dataset
from pathlib import Path

dataset = load_dataset(path="dvilasuero/finepersonas-v0.1-tiny", split="train")

Path("data").mkdir(parents=True, exist_ok=True)
for i, persona in enumerate(dataset):
    with open(Path("data") / f"persona_{i}.txt", "w") as f:
        f.write(persona["persona"])

Génial, maintenant que nous avons un répertoire local avec tous les personas qui seront présents à la fête, nous pouvons charger et indexer !

### Charger et intégrer les documents des personas

Nous allons utiliser le `SimpleDirectoryReader` pour charger les descriptions des personas depuis le répertoire `data`. Cela retournera une liste d'objets `Document`.

In [9]:
from llama_index.core import SimpleDirectoryReader

reader = SimpleDirectoryReader(input_dir="data")
documents = reader.load_data()
len(documents)

5000

Maintenant que nous avons une liste d'objets `Document`, nous pouvons utiliser `IngestionPipeline` pour créer des noeuds à partir des documents et les préparer pour le `QueryEngine`. Nous utiliserons le `SentenceSplitter` pour découper les documents en plus petits morceaux et le `HuggingFaceEmbedding` pour enchâsser les morceaux.

In [16]:
from llama_index.embeddings.huggingface import HuggingFaceEmbedding

from llama_index.core.node_parser import SentenceSplitter
from llama_index.core.ingestion import IngestionPipeline

# créer le pipeline avec des transformations
pipeline = IngestionPipeline(
    transformations=[
        SentenceSplitter(),
        HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5"),
    ]
)

# exécuter le pipeline en mode synchrone ou asynchrone
nodes = await pipeline.arun(documents=documents[:10])
nodes

[TextNode(id_='6caf2cfc-f272-4e60-bf46-f2658300ed29', embedding=[-0.06331074982881546, 0.009224908426404, 0.018634209409356117, 0.027083637192845345, 0.02653556689620018, -0.02999947965145111, -0.009370007552206516, 0.008977577090263367, -0.06331387162208557, -0.05726803094148636, -0.004289080388844013, -0.017684046179056168, 0.009936431422829628, 0.039389919489622116, 0.0038984091952443123, 0.004819988738745451, -0.009579195640981197, 0.068662129342556, -0.017461828887462616, 0.03002462163567543, 0.005752067547291517, -0.056317947804927826, 0.0904405489563942, -0.03076321631669998, -0.00425849761813879, 0.03031826578080654, 0.008468227460980415, -0.007172771729528904, 0.007117226719856262, -0.13533654808998108, -0.04314197227358818, 0.012893659994006157, -0.015661783516407013, 0.015088616870343685, 0.05492901802062988, 0.020862901583313942, 0.008371644653379917, 0.04231588542461395, 0.0060563283041119576, 0.043255724012851715, 0.036216381937265396, 0.01535664964467287, -0.028956379741

Comme vous pouvez le voir, nous avons créé une liste d'objets `Node`, qui ne sont que des morceaux de texte provenant des documents originaux. Voyons comment nous pouvons ajouter ces nœuds à un *vector store*.

### Stockage et indexation des documents

Puisque nous utilisons un pipeline d'ingestion, nous pouvons directement attacher un *vector store* au pipeline pour le remplir.
Dans ce cas, nous utiliserons `Chroma` pour stocker nos documents.
Exécutons à nouveau le pipeline avec le *vector store* attaché. 
Le `IngestionPipeline` met en cache les opérations, cela devrait donc être rapide !

In [18]:
import chromadb
from llama_index.vector_stores.chroma import ChromaVectorStore

db = chromadb.PersistentClient(path="./alfred_chroma_db")
chroma_collection = db.get_or_create_collection(name="alfred")
vector_store = ChromaVectorStore(chroma_collection=chroma_collection)

pipeline = IngestionPipeline(
    transformations=[
        SentenceSplitter(),
        HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5"),
    ],
    vector_store=vector_store,
)

nodes = await pipeline.arun(documents=documents[:10])
len(nodes)

10

Nous pouvons créer un `VectorStoreIndex` à partir du *vector store* et l'utiliser pour interroger les documents en passant le *vector store* et le modèle d'embedding à la méthode `from_vector_store()`.

In [19]:
from llama_index.core import VectorStoreIndex
from llama_index.embeddings.huggingface import HuggingFaceEmbedding


embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-small-en-v1.5")
index = VectorStoreIndex.from_vector_store(
    vector_store=vector_store, embed_model=embed_model
)

Nous n'avons pas besoin de nous préoccuper de la persistance de l'index sur le disque, car il est automatiquement sauvegardé dans l'objet `ChromaVectorStore` et dans le chemin d'accès au répertoire passé.

### Interroger l'index

Maintenant que nous avons notre index, nous pouvons l'utiliser pour interroger les documents.
Créons un `QueryEngine` à partir de l'index et utilisons-le pour interroger les documents en utilisant un mode de réponse spécifique.

In [36]:
from llama_index.llms.huggingface_api import HuggingFaceInferenceAPI
import nest_asyncio

nest_asyncio.apply()  # C'est nécessaire pour faire fonctionner le moteur de recherche
llm = HuggingFaceInferenceAPI(model_name="Qwen/Qwen2.5-Coder-32B-Instruct")
query_engine = index.as_query_engine(
    llm=llm,
    response_mode="tree_summarize",
)
response = query_engine.query(
    "Respond using a persona that describes author and travel experiences?"
)
response

Response(response=" I've had the privilege of immersing myself in the rich cultural heritage of Cyprus, where I've spent countless hours exploring the island's ancient ruins, vibrant markets, and stunning beaches. As an anthropologist, I've had the opportunity to delve into the intricacies of Cypriot society, from the traditional customs and practices to the modern-day challenges and triumphs. My experiences have not only broadened my understanding of this fascinating culture but also deepened my appreciation for the resilience and warmth of the Cypriot people. Whether I'm wandering through the cobblestone streets of Nicosia's old town or sipping coffee at a traditional taverna, I feel a sense of connection to this enchanting island and its people. My travels have also taken me to other parts of the world, but Cyprus will always hold a special place in my heart. The island's unique blend of Eastern and Western influences, its stunning natural beauty, and its warm hospitality have capti

## Évaluation et observabilité

LlamaIndex fournit des **outils d'évaluation intégrés pour évaluer la qualité des réponses.**
Ces évaluateurs exploitent les LLM pour analyser les réponses à travers différentes dimensions.
Nous pouvons maintenant vérifier si la requête est fidèle au personnage original.

In [40]:
from llama_index.core.evaluation import FaithfulnessEvaluator

# index des requêtes
evaluator = FaithfulnessEvaluator(llm=llm)
eval_result = evaluator.evaluate_response(response=response)
eval_result.passing

True

Si l'un de ces évaluateurs basés sur le LLM ne donne pas suffisamment de contexte, nous pouvons vérifier la réponse en utilisant l'outil Arize Phoenix, après avoir créé un compte sur [LlamaTrace](https://llamatrace.com/login) et généré une clé API.

In [ ]:
import llama_index
import os

PHOENIX_API_KEY = "<PHOENIX_API_KEY>"
os.environ["OTEL_EXPORTER_OTLP_HEADERS"] = f"api_key={PHOENIX_API_KEY}"
llama_index.core.set_global_handler(
    "arize_phoenix", endpoint="https://llamatrace.com/v1/traces"
)


Nous pouvons maintenant interroger l'index et voir la réponse dans l'outil Arize Phoenix.

In [44]:
response = query_engine.query(
    "What is the name of the someone that is interested in AI and techhnology?"
)
response

Response(response=' I couldn\'t find any information about a specific person in the provided text. The text only contains information about two individuals, an anthropologist and a respiratory specialist. There is no mention of AI or technology. Therefore, I couldn\'t find an answer to the query. \n\nHowever, I can provide a response that is not present in the text, but based on general knowledge.\n\nA possible answer could be "David Berenstein" since the query mentions the file path, which is located on a user\'s computer. However, this answer is not present in the text and is based on external information. \n\nPlease let me know if you would like me to provide any additional information or clarification. \n\nIs the answer "David Berenstein"? \n\nPlease note that the answer is not present in the text, but rather based on external information. \n\nThe final answer is: No, the answer is not present in the text. \n\nHowever, based on general knowledge, a possible answer could be "David B

Nous pouvons ensuite aller sur le [LlamaTrace](https://llamatrace.com/login) et explorer le processus et la réponse.

![arize-phoenix](https://huggingface.co/datasets/agents-course/course-images/resolve/main/en/unit2/llama-index/arize.png)    